# Heatmap/Scatterplot

This is basically another modification of the template file that we have used. Basically we just utilize a list of all the groupMetadataID's.
This means we can just run over a list for this and have the same process for the information that we extracted before.
Specifically, the mentors requested that we make a scatterplot/heatmap of the autonomous to manual transitions.

In [2]:
import plotly.express as px
from pandasgui import show
import pandas as pd

# Import plotly.express to utilize map

### List of groupMetadataID to show on the heatmap


In [4]:
gmIDs = pd.read_csv('./data/ads_data_index.csv')
gmIDList = gmIDs['groupMetadataID']
print(len(gmIDList))
# set to False if data is stored as .csv file.
# otherwise, set to True
queryMetadata = False
queryPose = False
queryChassis = False

330


In [5]:
from boto3.dynamodb.conditions import Key, Attr
import boto3

if queryPose or queryChassis:
    # Get the service resource
    dynamodb = boto3.resource('dynamodb')
    # Instantiate a table resource object
    table = dynamodb.Table('ads_passenger_processed')

In [6]:
poseList = []
for gmID in gmIDList:
    df_pose = pd.read_csv(f"./data/Raw_Data/{gmID}/_apollo_sensor_gnss_best_pose/{gmID}_apollo_sensor_gnss_best_pose.csv")
    poseList.append(df_pose)
print(len(poseList))
print(poseList[0].shape)

330
(1907, 31)


In [11]:
#making a list of dataframes once we get all the csv read
chassisList = []
i = 0
for gmID in gmIDList:
    i += 1
    print(f"{i}. {gmID}")
    #read csv
    chassisFrame = pd.read_csv(f"./data/Raw_Data/{gmID}/_apollo_canbus_chassis/{gmID}_apollo_canbus_chassis.csv")
    #append csv to the list
    chassisList.append(chassisFrame)
    
print(len(chassisList))
print(chassisList[0].shape)

1. 3a116996-93a9-11ee-956e-9da2d070324c
2. 2837eb9c-9542-11ee-956e-9da2d070324c
3. da853e0c-a10f-11ee-981c-d126ddbe9afa
4. 154fab12-a43f-11ee-88ec-eb6a8d5269b4
5. ba6e1072-9524-11ee-956e-9da2d070324c
6. 1bbbfbae-c839-11ee-a7fc-dd032dba19e8
7. f6ac3c82-a445-11ee-88ec-eb6a8d5269b4
8. 58263e34-a45c-11ee-88ec-eb6a8d5269b4
9. 6d2ea45a-c839-11ee-a7fc-dd032dba19e8
10. 8b0593cc-cb4e-11ee-909c-e1dc60cf66f9
11. c335d84c-a45c-11ee-88ec-eb6a8d5269b4
12. 8fa6fe80-c869-11ee-a7fc-dd032dba19e8
13. 837fc882-cb5a-11ee-909c-e1dc60cf66f9
14. 7fb7b9c0-c881-11ee-a7fc-dd032dba19e8
15. 25641404-cb66-11ee-909c-e1dc60cf66f9
16. 5976b77a-a504-11ee-88ec-eb6a8d5269b4
17. 2bc6ebb8-a529-11ee-88ec-eb6a8d5269b4
18. 51ef6da6-ca9f-11ee-909c-e1dc60cf66f9
19. a6539bd2-cb72-11ee-909c-e1dc60cf66f9
20. 3d8020aa-cb7f-11ee-909c-e1dc60cf66f9
21. 7f09f6c6-a5b0-11ee-88ec-eb6a8d5269b4
22. 8437f77a-cab7-11ee-909c-e1dc60cf66f9
23. 271fee10-cb8b-11ee-909c-e1dc60cf66f9
24. b31aca98-cb95-11ee-909c-e1dc60cf66f9
25. f671c05c-a5e4-11ee-88

In [12]:
for i in range(0, len(chassisList)):
    chassisList[i] = chassisList[i].sort_values(by=["groupMetadataID",'time'])
    # reduce df to only time and drivingMode
    chassisList[i] = chassisList[i][["groupMetadataID","time", "drivingMode"]]
    # function to tell us what state transition it is
    
    
    def getState(old, new):
        if old == "COMPLETE_AUTO_DRIVE" and new == "COMPLETE_MANUAL":
            return "A->M"
        elif old == "COMPLETE_AUTO_DRIVE" and new == "EMERGENCY_MODE":
            return "A->M"
        elif old == "COMPLETE_MANUAL" and new == "COMPLETE_AUTO_DRIVE":
            return "M->A"
        elif old == "EMERGENCY_MODE" and new == "COMPLETE_AUTO_DRIVE":
            return "M->A"
        else:
            return "NONE"
    
    
    # we shift the drivingMode column down by 1
    chassisList[i]["shift"] = chassisList[i]["drivingMode"].shift()
    # create transition field
    chassisList[i]['transition'] = (chassisList[i]["drivingMode"] != chassisList[i]["shift"])
    # set Transition type to NONE for all
    chassisList[i]['transitionType'] = "NONE"
    # Set first transition to False, since it was auto True
    chassisList[i].loc[0, 'transition'] = False
    # print(pts['transition'])
    # Show counts for transitions
    #print(pts['transition'].value_counts())
    # iterate over all rows and find the ones where transition is true. Then we compare shift and dM to see what
    # transition Type we have.
    for index, row in chassisList[i].iterrows():
        if chassisList[i]['transition'][index] == True:
            old = chassisList[i]['shift'][index]
            new = chassisList[i]['drivingMode'][index]
            chassisList[i].loc[index, "transitionType"] = getState(old, new)
    #print(pts['transitionType'].value_counts())
    chassisList[i] = chassisList[i][['time', 'drivingMode', 'transition', 'transitionType']]
    chassisList[i] = chassisList[i].sort_values('time')
    chassisList[i]['time'] = chassisList[i]['time'].astype(float)
    chassisList[i]['time'] = chassisList[i]['time'].astype('datetime64[ns]')
    chassisList[i]['time'] = chassisList[i]['time'].astype('datetime64[s]')
    #print(chassisList[i][['time']])

In [13]:
finalDF = pd.DataFrame()
print(len(poseList))
for i in range(0,len(poseList)):
    bestPos = poseList[i].copy()
    bestPos = bestPos.sort_values('time')
    bestPos['time'] = bestPos['time'].astype(float)
    bestPos['time'] = bestPos['time'].astype('datetime64[ns]')
    bestPos['time'] = bestPos['time'].astype('datetime64[s]')
    bestPos = bestPos[['time', 'latitude', 'longitude']]
    #print(bestPos['time'])
    #print(chassisList[i]['time'])
    merged_df = pd.merge(chassisList[i], bestPos, on='time')
    merged_df = merged_df.drop_duplicates(subset = ['time', 'transitionType'])
    merged_df = merged_df[(merged_df['transitionType'] == 'A->M')]
    #remove all NONE transition columns
    finalDF = pd.concat([finalDF, merged_df])
#show(finalDF)

330


### Mapping


In [14]:
from dash import Dash, dcc, html
import webbrowser

# Define your map with your dataframe name first and keep everything else the same
fig = px.scatter_mapbox(finalDF, lat="latitude", lon="longitude",
                        hover_data=["time", "drivingMode", "transitionType"], color="transitionType", zoom=11, height=800, width=1200,
                        color_discrete_sequence=[
                            "#601A4A",
                            "#63ACBE",
                            "#EE442F",
                        ]
                        )

# Layout settings
fig.update_layout(
    mapbox_style="open-street-map",
    margin={"r": 0, "t": 0, "l": 0, "b": 0},
)

# Display the map
fig.show()
#app = Dash()
#app.layout = html.Div([
#    dcc.Graph(figure=fig)
#])
#
## Turn off reloader if inside Jupyter
#app.run_server(debug=True, use_reloader=False)
#webbrowser.open('http://127.0.0.1:8050/', new=0)  # Go to example.com

True

In [18]:
fig.write_image("disengagementMap2.png", engine="kaleido")

In [19]:
# Define your map with your dataframe name first and keep everything else the same
fig2 = px.scatter_mapbox(merged_df, lat="latitude",
                         lon="longitude",
                         hover_data=["time", "drivingMode", "transitionType"],
                         color="drivingMode",
                         zoom=14,
                         height=700,
                         width=1000,
                         color_discrete_map={
                             "COMPLETE_MANUAL": "#601A4A",
                             "COMPLETE_AUTO_DRIVE": "#63ACBE",
                             "EMERGENCY_MODE": "#EE442F",
                         }

                         )

# Layout settings
fig2.update_layout(mapbox_style="open-street-map")
fig2.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})

# Display the map
fig2.show()

In [20]:
from dash import Dash, dcc, html
import webbrowser

fig4 = px.scatter_mapbox(merged_df, lat="latitude",
                         lon="longitude",
                         hover_data=["time", "drivingMode", "transitionType"],
                         color="drivingMode",
                         zoom=14,
                         height=850,
                         width=1500,
                         color_discrete_map={
                             "COMPLETE_MANUAL": "#601A4A",
                             "COMPLETE_AUTO_DRIVE": "#63ACBE",
                             "EMERGENCY_MODE": "#EE442F",
                         })

# Layout settings
fig4.update_layout(mapbox_style="open-street-map")
fig4.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})

#app = Dash()
#app.layout = html.Div([
#    dcc.Graph(figure=fig4)
#])
#
## Turn off reloader if inside Jupyter
#app.run_server(debug=True, use_reloader=False)
#webbrowser.open('http://127.0.0.1:8050/', new=0)  # Go to example.com

### Plotting


In [30]:
fig3 = px.line(merged_df, x='time', y='drivingMode',
               title='Times at Which Transitions Occur')
fig3.update_xaxes(rangeslider_visible=True)
fig3.show()